# Experiment Template


**In this notebook:**

* Load original mri data + aneurysm mask
* Resample Images to 1.5 mm Voxelsize
* Filter images based on size
* Train network to predict vessel mask
* Evaluate aneurysm mask

**Todo:**
* Check percentage of 1s in resampled mask
* Write evaluation
* Try out different batch_sizes

## Dependencies
Install, load, and initialize all required dependencies for this experiment.

### Install Dependencies

In [1]:
#It should be possible to run the notebook independent of anything else. 
# If dependency cannot be installed via pip, either:
# - download & install it via %%bash
# - atleast mention those dependecies in this section

import sys
!{sys.executable} -m pip install -q -e ../../utils/


You should consider upgrading via the '/group/cake/leo/.venv/bin/python -m pip install --upgrade pip' command.


In [2]:
!{sys.executable} -m pip install tqdm


You should consider upgrading via the '/group/cake/leo/.venv/bin/python -m pip install --upgrade pip' command.


In [1]:
x =5
a = x
del a 
print(x)

5


### Import Dependencies

# System libraries

In [1]:
from __future__ import absolute_import, division, print_function
import logging, os, sys

# Enable logging
logging.basicConfig(format='[%(levelname)s] %(message)s', level=logging.INFO, stream=sys.stdout)

# Re-import packages if they change
%load_ext autoreload
%autoreload 2

# Recursion Depth
import sys
sys.setrecursionlimit(10000)

# Intialize tqdm to always use the notebook progress bar
import tqdm
tqdm.tqdm = tqdm.tqdm_notebook

# Third-party libraries
import comet_ml
import numpy as np
import pandas as pd
import nilearn.plotting as nip
import matplotlib.pyplot as plt
import nibabel as nib
import numpy as np
import collections
%matplotlib inline
plt.rcParams["figure.figsize"] = (12,6)
%config InlineBackend.figure_format='retina'  # adapt plots for retina displays
import git


# Project utils

import aneurysm_utils
from aneurysm_utils import evaluation, training


/group/cake/leo/.venv/lib/python3.8/site-packages/nilearn/datasets/__init__.py:87: FutureWarning: Fetchers from the nilearn.datasets module will be updated in version 0.9 to return python strings instead of bytes and Pandas dataframes instead of Numpy arrays.
  warn("Fetchers from the nilearn.datasets module will be "


Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.


In [2]:
if "workspace" in os.getcwd():
    ROOT = "/workspace"
elif "/group/cake" in os.getcwd(): 
    ROOT = "/group/cake"


### Initialize Environment

In [3]:
env = aneurysm_utils.Environment(project="our-git-project", root_folder=ROOT)
env.cached_data["comet_key"] = "EGrR4luSis87yhHbs2rEaqAWs" 
env.print_info()

Environment Info:

Library Version: 0.1.0
Configured Project: our-git-project

Folder Structure: 
- Root folder: /group/cake
 - Project folder: /group/cake/our-git-project
 - Datasets folder: /data/training
 - Models folder: /group/cake/our-git-project/models
 - Experiments folder: /group/cake/our-git-project/experiments


## Load Data
Download, explore, and prepare all required data for the experiment in this section.

In [4]:
dataset_params = {
    "prediction": "mask",
    "mri_data_selection": "", 
    "balance_data": False,
    "seed": 1,
     "resample_voxel_dim": (1.0,1.0,1.0)
    #"resample_size":(93,93,80)
    
}

preprocessing_params = {
    'min_max_normalize': True,
    'mean_std_normalize': False,
    'smooth_img': False, # can contain a number: smoothing factor
    'intensity_segmentation': None
}


### Load Meta Data

In [5]:
from aneurysm_utils.data_collection import load_aneurysm_dataset

df = load_aneurysm_dataset(
    env,
    mri_data_selection=dataset_params["mri_data_selection"],
    random_state=dataset_params["seed"]
)
df.head()

Aneurysm Geometry  Angiography Data  Vessel Geometry  Labeled Mask Index  \
0          A001.stl  A001_orig.nii.gz  A001_vessel.stl                   1   
1          A003.stl  A003_orig.nii.gz  A003_vessel.stl                   1   
2          A005.stl  A005_orig.nii.gz  A005_vessel.stl                   1   
3          A006.stl  A006_orig.nii.gz  A006_vessel.stl                   1   
4          A008.stl  A008_orig.nii.gz  A008_vessel.stl                   1   

  Location  Age Sex  Rupture Status   Age Bin  Aneurysm Count  Case  \
0     Acom   48   m             1.0  (40, 50]               1  A001   
1     Pcom   58   f             0.0  (50, 60]               1  A003   
2     PICA   45   m             1.0  (40, 50]               1  A005   
3     ACom   46   f             1.0  (40, 50]               1  A006   
4      ACA   72   f             0.0  (70, 80]               1  A008   

                         Path Orig                         Path Mask  \
0  /data/training/A001_orig.nii.gz  /data/training/A001_masks.nii.gz   
1  /data/training/A003_orig.nii.gz  /data/training/A003_masks.nii.gz   
2  /data/training/A005_orig.nii.gz  /data/training/A005_masks.nii.gz   
3  /data/training/A006_orig.nii.gz  /data/training/A006_masks.nii.gz   
4  /data/training/A008_orig.nii.gz  /data/training/A008_masks.nii.gz   

                         Path Vessel                        Path Labeled Mask  
0  /data/training/A001_vessel.nii.gz  /data/training/A001_labeledMasks.nii.gz  
1  /data/training/A003_vessel.nii.gz  /data/training/A003_labeledMasks.nii.gz  
2  /data/training/A005_vessel.nii.gz  /data/training/A005_labeledMasks.nii.gz  
3  /data/training/A006_vessel.nii.gz  /data/training/A006_labeledMasks.nii.gz  
4  /data/training/A008_vessel.nii.gz  /data/training/A008_labeledMasks.nii.gz

### Load & Split MRI Data

In [6]:
# Load MRI images and split into train, test, and validation
from aneurysm_utils.data_collection import split_mri_images
# case_list = ["A009","A010","A012","A016","A014","A015"]
# df = df.loc[df["Case"].isin(case_list)]

train_data, test_data, val_data, _ = split_mri_images(
    env, 
    df, 
    prediction=dataset_params["prediction"], 
    encode_labels=False,
    random_state=dataset_params["seed"],
    balance_data=dataset_params["balance_data"],
    resample_voxel_dim=dataset_params["resample_voxel_dim"],
    #resample_size=dataset_params["resample_size"]
)

mri_imgs_train, labels_train = train_data
mri_imgs_test, labels_test = test_data
mri_imgs_val, labels_val = val_data

109
98
         Images
-----  --------
All         109
Train        87
Val          11
Test         11



  0%|          | 0/87 [00:00<?, ?it/s]

  0%|          | 0/11 [00:00<?, ?it/s]

  0%|          | 0/11 [00:00<?, ?it/s]

In [7]:
dataset_params = {
    "prediction": "vessel",
    "mri_data_selection": "", 
    "balance_data": False,
    "seed": 1,
    "resample_voxel_dim": (1.0,1.0,1.0),
    #"resample_size":(93,93,80)
    
}

preprocessing_params = {
    'min_max_normalize': True,
    'mean_std_normalize': False,
    'smooth_img': False, # can contain a number: smoothing factor
    'intensity_segmentation': None
}

from aneurysm_utils.data_collection import load_aneurysm_dataset

df = load_aneurysm_dataset(
    env,
    mri_data_selection=dataset_params["mri_data_selection"],
    random_state=dataset_params["seed"]
)
df.head()

# Load MRI images and split into train, test, and validation
from aneurysm_utils.data_collection import split_mri_images
# case_list = ["A009","A010","A012","A016","A014","A015"]
# df = df.loc[df["Case"].isin(case_list)]

train_data, test_data, val_data, _ = split_mri_images(
    env, 
    df, 
    prediction=dataset_params["prediction"], 
    encode_labels=False,
    random_state=dataset_params["seed"],
    balance_data=dataset_params["balance_data"],
    resample_voxel_dim=dataset_params["resample_voxel_dim"],
    #resample_size=dataset_params["resample_size"]
)

_, labels_train_vessel = train_data
_, labels_test_vessel = test_data
_, labels_val_vessel = val_data



109
98
         Images
-----  --------
All         109
Train        87
Val          11
Test         11



  0%|          | 0/87 [00:00<?, ?it/s]

  0%|          | 0/11 [00:00<?, ?it/s]

  0%|          | 0/11 [00:00<?, ?it/s]

In [13]:
mri_imgs_train= [img *mask for img,mask in zip(mri_imgs_train,labels_train_vessel)]
mri_imgs_test= [img *mask for img,mask in zip(mri_imgs_test,labels_test_vessel)]
mri_imgs_val= [img *mask for img,mask in zip(mri_imgs_val,labels_val_vessel)]

ValueError: operands could not be broadcast together with shapes (139,139,120) (139,139,119) 

In [18]:
print(np.count_nonzero(mri_imgs_train[0]))

1359


In [19]:
from aneurysm_utils import preprocessing

most_common_shape=preprocessing.check_mri_shapes(mri_imgs_train)
print(most_common_shape)


Most common:
(139, 139, 120):      75
(139, 139, 120)


## Transform & Preprocess Data

In [20]:
from aneurysm_utils import preprocessing

size_of_train = len(mri_imgs_train)
size_of_test = len(mri_imgs_test)
size_of_val = len(mri_imgs_val)

# preprocess all lists as one to have a working mean_std_normalization
mri_imgs = mri_imgs_train + mri_imgs_test + mri_imgs_val
mri_imgs = preprocessing.preprocess(env, mri_imgs, preprocessing_params)

mri_imgs_train = mri_imgs[:size_of_train]
mri_imgs_train = [train for train in mri_imgs_train]
mri_imgs_test = mri_imgs[size_of_train : size_of_train + size_of_test]
mri_imgs_test = [test for test in mri_imgs_test]
mri_imgs_val = mri_imgs[size_of_train + size_of_test :]
mri_imgs_val = [val for val in mri_imgs_val]

# preprocess mask
x, y, h = labels_train[0].shape
labels_train = [label_train for label_train in labels_train]
labels_test = [label_test for label_test in labels_test]
labels_val = [label_val for label_val in labels_val]
# flatten

[INFO] Preprocessing: Min Max Normalize...


In [21]:
size = (139, 139, 120)#(93, 93, 80)  #(139, 139, 120)#(47,47,41)#
print(size)
train_index = [i for i, e in enumerate(mri_imgs_train) if e.shape != size]
mri_imgs_train = [i for j, i in enumerate(mri_imgs_train) if j not in train_index]
labels_train = [i for j, i in enumerate(labels_train) if j not in train_index]

test_index = [i for i, e in enumerate(mri_imgs_test) if e.shape != size]
mri_imgs_test = [i for j, i in enumerate(mri_imgs_test) if j not in test_index]
labels_test = [i for j, i in enumerate(labels_test) if j not in test_index]

val_index = [i for i, e in enumerate(mri_imgs_val) if e.shape != size]
mri_imgs_val = [i for j, i in enumerate(mri_imgs_val) if j not in val_index]
labels_val = [i for j, i in enumerate(labels_val) if j not in val_index]

mri_imgs_train[0].shape
preprocessing.check_mri_shapes(mri_imgs_train)
print(np.unique(labels_val[0], return_counts=True))


(139, 139, 120)
Most common:
(139, 139, 120):      75
(array([0., 1.], dtype=float32), array([2318414,     106]))


## Train Model
Implementation, configuration, and evaluation of the experiment.

### Train Deep Model 3D data

In [22]:
from comet_ml import Optimizer

artifacts = {
    "train_data": (mri_imgs_train, labels_train),
    "val_data": (mri_imgs_val, labels_val),
    "test_data": (mri_imgs_test, labels_test)
}

# Define parameter configuration for experiment run
# params = {
#     "batch_size": 3,
#     "epochs": 10,
#     "es_patience": None, # None = deactivate early stopping
#     "model_name": 'SegNet',
#     "optimizer_momentum": 0.9,
#     "optimizer":'Adam',
#     "learning_rate": 0.0001,
#     "criterion": "CrossEntropyLoss",
#     "sampler": None,   #'ImbalancedDatasetSampler2',
#     "shuffle_train_set": True,
#     "save_models": False,
#     "criterion_weights": [1.0, 1000.0],
#     "debug": True,
#     "weight_decay":0.01
# }
params = {
    "batch_size": 16,
    "epochs": 250,
    "learning_rate": 5.0e-3, # 3e-04, 1.0E-5
    "es_patience": None, # None = deactivate early stopping
    "weight_decay": 0.001, # 1e-3
    "model_name": 'SegNet',
    "optimizer_momentum": 0.9,
    "optimizer":'Adam',
    "criterion": "CrossEntropyLoss", 
    "criterion_weights": [1.0, 10.0], # [1.75, 1.0],
    "sampler": None,   #'ImbalancedDatasetSampler2',
    "shuffle_train_set": True,
    "save_models":True,
    "scheduler": "ReduceLROnPlateau", # "ReduceLROnP
    "debug":False,
    "dropout":0.2,
    "start_radius":0.2*int(most_common_shape[0]),
    "save_models":True
    
}
params.update(dataset_params)
params.update(preprocessing_params)
config = {
    # We pick the Bayes algorithm:
    "algorithm": "bayes",
    # Declare your hyperparameters in the Vizier-inspired format:
    "parameters": {
        "criterion_weights": {"type": "integer", "scalingType": "loguniform", "min": 1, "max": 20},
        "weight_decay": {"type": "float", "scalingType": "loguniform", "min": 1e-10, "max": 1e-3},
        "learning_rate": {"type": "float", "scalingType": "loguniform", "min": 1e-10, "max": 1e2},
        "scheduler": {"type": "categorical", "values": ["ReduceLROnPlateau", ""],},
        "start_radius":{"type":"float","scalingType":"loguniform","min":0.1, "max":0.2},
    },
    # Declare what we will be optimizing, and how:
    "spec": {"metric": "bal_acc", "objective": "maximize"},  #test balance accuracy
}


opt = Optimizer(config, api_key=env.cached_data["comet_key"])

COMET INFO: COMET_OPTIMIZER_ID=462dfec7e81b4037ac91b8af2d829893
COMET INFO: Using optimizer config: {'algorithm': 'bayes', 'configSpaceSize': 'infinite', 'endTime': None, 'id': '462dfec7e81b4037ac91b8af2d829893', 'lastUpdateTime': None, 'maxCombo': 0, 'name': '462dfec7e81b4037ac91b8af2d829893', 'parameters': {'criterion_weights': {'max': 20, 'min': 1, 'scalingType': 'loguniform', 'type': 'integer'}, 'learning_rate': {'max': 100.0, 'min': 1e-10, 'scalingType': 'loguniform', 'type': 'float'}, 'scheduler': {'type': 'categorical', 'values': ['ReduceLROnPlateau', '']}, 'start_radius': {'max': 0.2, 'min': 0.1, 'scalingType': 'loguniform', 'type': 'float'}, 'weight_decay': {'max': 0.001, 'min': 1e-10, 'scalingType': 'loguniform', 'type': 'float'}}, 'predictor': None, 'spec': {'gridSize': 10, 'maxCombo': 0, 'metric': 'bal_acc', 'minSampleSize': 100, 'objective': 'maximize', 'retryAssignLimit': 0, 'retryLimit': 1000}, 'startTime': 14781652337, 'state': {'mode': None, 'seed': None, 'sequence': [

In [23]:
import gc
gc.collect()

170

In [24]:
# Finally, get experiments, and train your models:
import time
for comet_exp in opt.get_experiments(project_name=env.project):
    print(comet_exp)
    param_copy = params.copy()
    comet_exp.params
    
    param_copy["weight_decay"] = comet_exp.get_parameter("weight_decay")
    param_copy["criterion_weights"] = comet_exp.get_parameter("criterion_weights")
    param_copy["learning_rate"] = comet_exp.get_parameter("learning_rate")
    param_copy["scheduler"] = comet_exp.get_parameter("scheduler")

    exp = env.create_experiment(
        params["prediction"] + "-pytorch-" + params["model_name"], comet_exp
    ) #params["selected_label"] + "-hyperopt-" + params["model_name"]
    exp.run(training.train_pytorch_model, param_copy, artifacts)
    
    time.sleep(3)
    del exp
    import gc
    gc.collect()


COMET WARNING: As you are running in a Jupyter environment, you will need to call `experiment.end()` when finished to ensure all metrics and code are logged before exiting.
COMET INFO: Experiment is live on comet.ml https://www.comet.ml/rbendias/our-git-project/bcb8f38a5f9d40929e216dbae68c7021



[INFO] Experiment vessel-pytorch-SegNet is initialized.
[INFO] Running experiment: 2021-07-11-23-25-04_vessel-pytorch-segnet
Number of Classes 2
---Parameters Loading took 4.215341806411743 seconds ---
Selected model: SegNet
---Model Loading took 5.064446210861206 seconds ---
Processing...
Done!
Processing...
Done!
Processing...
Done!
[INFO] Train dataset loaded. Length: 75
[INFO] Validation dataset loaded. Length: 9
[INFO] Engine run starting with max_epochs=250.


Argument save_interval is deprecated and should be None. This argument will be removed in 0.5.0.Please, use events filtering instead, e.g. Events.ITERATION_STARTED(every=1000)


[INFO] Engine run starting with max_epochs=1.
[INFO] Epoch[1] Complete. Time taken: 00:00:01
[INFO] Learning rate: 1.3457567957765812e-09
[INFO] Engine run complete. Time taken: 00:00:01
[INFO] Training Results - Epoch: 1 Bal Avg accuracy: 0.50 Avg loss: 0.69
RAM memory % used: 19.2
[INFO] Engine run starting with max_epochs=1.
[INFO] Epoch[1] Complete. Time taken: 00:00:00
[INFO] Learning rate: 1.3457567957765812e-09
[INFO] Engine run complete. Time taken: 00:00:00
[INFO] Validation Results - Epoch: 1 Bal Avg accuracy: 0.50 Avg loss: 0.69
RAM memory % used: 19.1
[INFO] Epoch[1] Complete. Time taken: 00:00:03
[INFO] Engine run starting with max_epochs=1.
[INFO] Epoch[1] Complete. Time taken: 00:00:01
[INFO] Learning rate: 1.3457567957765812e-09
[INFO] Engine run complete. Time taken: 00:00:01
[INFO] Training Results - Epoch: 2 Bal Avg accuracy: 0.50 Avg loss: 0.69
RAM memory % used: 19.1
[INFO] Engine run starting with max_epochs=1.
[INFO] Epoch[1] Complete. Time taken: 00:00:00
[INFO]

Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.


...

[INFO] Experiment vessel-pytorch-SegNet is initialized.
[INFO] Running experiment: 2021-07-12-10-20-39_vessel-pytorch-segnet
Number of Classes 2
---Parameters Loading took 4.21782112121582 seconds ---
Selected model: SegNet
---Model Loading took 0.046811819076538086 seconds ---
Processing...
Done!
Processing...
Done!
Processing...
Done!
[INFO] Train dataset loaded. Length: 75
[INFO] Validation dataset loaded. Length: 9
[INFO] Engine run starting with max_epochs=250.


Argument save_interval is deprecated and should be None. This argument will be removed in 0.5.0.Please, use events filtering instead, e.g. Events.ITERATION_STARTED(every=1000)


[INFO] Engine run starting with max_epochs=1.
[INFO] Epoch[1] Complete. Time taken: 00:00:01
[INFO] Learning rate: 5.827267170613941e-05
[INFO] Engine run complete. Time taken: 00:00:01
[INFO] Training Results - Epoch: 1 Bal Avg accuracy: 0.50 Avg loss: 0.70
RAM memory % used: 20.2
[INFO] Engine run starting with max_epochs=1.
[INFO] Epoch[1] Complete. Time taken: 00:00:00
[INFO] Learning rate: 5.827267170613941e-05
[INFO] Engine run complete. Time taken: 00:00:00
[INFO] Validation Results - Epoch: 1 Bal Avg accuracy: 0.50 Avg loss: 0.70
RAM memory % used: 20.2
[INFO] Epoch[1] Complete. Time taken: 00:00:04
[INFO] Engine run starting with max_epochs=1.
[INFO] Epoch[1] Complete. Time taken: 00:00:01
[INFO] Learning rate: 5.827267170613941e-05
[INFO] Engine run complete. Time taken: 00:00:01
[INFO] Training Results - Epoch: 2 Bal Avg accuracy: 0.50 Avg loss: 0.70
RAM memory % used: 20.2
[INFO] Engine run starting with max_epochs=1.
[INFO] Epoch[1] Complete. Time taken: 00:00:00
[INFO] Le

COMET INFO: Optimizer metrics is 'bal_acc' but no logged values found. Experiment ignored in sweep.
COMET INFO: ---------------------------
COMET INFO: Comet.ml Experiment Summary
COMET INFO: ---------------------------
COMET INFO:   Data:
COMET INFO:     display_summary_level : 1
COMET INFO:     url                   : https://www.comet.ml/rbendias/our-git-project/5f32370bd0e04156b7c14f1f3077a037
COMET INFO:   Metrics [count] (min, max):
COMET INFO:     loss                  : 0.7110128402709961
COMET INFO:     train_accuracy [3]    : (0.42851679491314565, 0.8205593696723955)
COMET INFO:     train_avg_loss [3]    : (0.6927085253190803, 0.7017874113025849)
COMET INFO:     train_bal_acc [3]     : (0.5, 0.5004798700910165)
COMET INFO:     train_curr_epoch [3]  : (1, 3)
COMET INFO:     train_lr              : 5.827267170613941e-05
COMET INFO:     train_sen [3]         : (0.0, 0.6127259654889071)
COMET INFO:     train_spec [3]        : (0.3882337746931258, 1.0)
COMET INFO:     validate_acc

RuntimeError: CUDA out of memory. Tried to allocate 186.00 MiB (GPU 0; 10.76 GiB total capacity; 6.68 GiB already allocated; 63.56 MiB free; 7.71 GiB reserved in total by PyTorch)

# Run experiment and sync all metadata
exp = env.create_experiment(
    params["prediction"] + "-pytorch-" + params["model_name"],
    comet_ml.Experiment(
        env.cached_data["comet_key"],
        project_name=env.project + "-" + params["prediction"],
        disabled=params["debug"],
    ),
)
exp.run(training.train_pytorch_model, params, artifacts)

## Evaluate Model

Do evaluation, e.g. visualizations  

In [ ]:
from aneurysm_utils.utils.pytorch_utils import predict

In [ ]:
model = exp.artifacts["model"]

In [ ]:
predictions = predict(model, mri_imgs_val, apply_softmax=False )

In [ ]:
predictions[0][1]

In [ ]:

idx = 0
nip.view_img(
    nib.Nifti1Image(predictions[0][0], np.eye(4)),
    symmetric_cmap=False,
    cmap="Greys_r",
    bg_img=False,
    black_bg=True,
    threshold=1e-03, 
    draw_cross=False
)

In [ ]:
idx = 0
nip.view_img(
    nib.Nifti1Image(labels_val[0], np.eye(4)),
    symmetric_cmap=False,
    cmap="Greys_r",
    bg_img=False,
    black_bg=True,
    threshold=1e-03, 
    draw_cross=False
)